In [23]:
import os
import json
import numpy as np
import re

In [24]:
import cv2
import matplotlib.pyplot as plt

In [26]:
import numpy as np

In [27]:
with open("/home/winnie/Project/road_dataset/coco/annotations/instances_train2017.json", "r") as f:
    train_data = json.load(f)

In [28]:
len(train_data['images'])

2762

In [29]:
train_data['images']

[{'license': 1,
  'file_name': '031_4875.png',
  'width': 1280,
  'id': 20485447352320001,
  'height': 720},
 {'license': 1,
  'file_name': '029_12075.png',
  'width': 1920,
  'id': 20485448891629574,
  'height': 1208},
 {'license': 1,
  'file_name': '031_2600.png',
  'width': 1280,
  'id': 20485450363830280,
  'height': 720},
 {'license': 1,
  'file_name': '031_6700.png',
  'width': 1280,
  'id': 20485451882168323,
  'height': 720},
 {'license': 1,
  'file_name': '031_5650.png',
  'width': 1280,
  'id': 20485453379534853,
  'height': 720},
 {'license': 1,
  'file_name': '031_875.png',
  'width': 1280,
  'id': 20485454885289986,
  'height': 720},
 {'license': 1,
  'file_name': '024_03450.jpg',
  'width': 1920,
  'id': 20485455262777348,
  'height': 1080},
 {'license': 1,
  'file_name': '027_24550.png',
  'width': 1920,
  'id': 20485455690596354,
  'height': 1208},
 {'license': 1,
  'file_name': '027_3250.png',
  'width': 1920,
  'id': 20485457234100225,
  'height': 1208},
 {'license': 

## Label

In [30]:
label_number = np.zeros(74, dtype = int)

train_annos = train_data["annotations"]

for anno in train_annos:
    anno_category = anno["category_id"]
    label_number[anno_category-1] += 1

In [31]:
label_name = ['Car', 'Truck', 'Bus', 'Tricycle', 'Motorcycle', 'Bicycle', 'Pedestrian', 'Traffic_Cone', 'Traffic_Bar', 
'Traffic_Barrier', 'Other_Barrier', 'Wheel', 'Go', 'Warning', 'Stop', 'GoStraight', 'WarningStraight', 
'StopStraight', 'GoLeft', 'WarningLeft', 'StopLeft', 'GoRight', 'WarningRight', 'StopRight', 'GoTurnAround', 
'WarningTurnAround', 'StopTurnAround', 'LightOff', 'I2', 'I4', 'I5', 'I6', 'Ip', 'P1', 'P5', 'P6', 'P9', 'P10', 
'P11', 'P12', 'P14', 'P19', 'P23', 'P26', 'Pb', 'Pc', 'Pg', 'Pl30', 'Pl40', 'Pl60', 'Pl70', 'Pl80', 'Pl100', 
'Pl110', 'Pl120', 'Pn', 'Pne', 'Ps', 'W3', 'W8', 'W9', 'W10', 'W11', 'W18', 'W20', 'W23', 'W24', 'W30', 'W47', 
'W55', 'W57', 'W58', 'W59', 'W63']

In [32]:
for (name, number) in zip(label_name, label_number):
    print(name, ": ", number)

Car :  8832
Truck :  2464
Bus :  452
Tricycle :  314
Motorcycle :  1282
Bicycle :  738
Pedestrian :  652
Traffic_Cone :  534
Traffic_Bar :  3226
Traffic_Barrier :  1304
Other_Barrier :  322
Wheel :  10886
Go :  582
Stop :  456
GoStraight :  110
WarningStraight :  0
StopStraight :  138
GoLeft :  100
WarningLeft :  6
StopLeft :  222
GoRight :  130
WarningRight :  0
StopRight :  0
GoTurnAround :  0
WarningTurnAround :  0
StopTurnAround :  24
LightOff :  408
I2 :  44
I4 :  34
I5 :  308
I6 :  0
Ip :  350
P1 :  8
P5 :  24
P6 :  58
P9 :  72
P10 :  70
P11 :  42
P12 :  78
P14 :  44
P19 :  24
P23 :  86
P26 :  204
Pb :  0
Pc :  4
Pg :  76
Pl30 :  20
Pl40 :  40
Pl60 :  160
Pl70 :  52
Pl80 :  30
Pl100 :  0
Pl110 :  0
Pl120 :  0
Pn :  136
Pne :  154
Ps :  46
W3 :  0
W8 :  0
W9 :  0
W10 :  0
W11 :  0
W18 :  0
W20 :  6
W23 :  0
W24 :  8
W30 :  22
W47 :  0
W55 :  2
W57 :  84
W58 :  0
W59 :  26
W63 :  0


In [33]:
label_number

array([ 8832,  2464,   452,   314,  1282,   738,   652,   534,  3226,
        1304,   322, 10886,   582,    30,   456,   110,     0,   138,
         100,     6,   222,   130,     0,     0,     0,     0,    24,
         408,    44,    34,   308,     0,   350,     8,    24,    58,
          72,    70,    42,    78,    44,    24,    86,   204,     0,
           4,    76,    20,    40,   160,    52,    30,     0,     0,
           0,   136,   154,    46,     0,     0,     0,     0,     0,
           0,     6,     0,     8,    22,     0,     2,    84,     0,
          26,     0])

## Get infos

#### 1. train_dic

In [34]:
image_infos = train_data['images']
anno_infos = train_data['annotations']
train_dic = dict()

In [35]:
def add_image_info(image_info):
    global train_dic
    
    image_id = image_info["id"]
    if image_id in train_dic.keys():
        print("duplicate image id! Image id is: " + str(image_id))
    else:
        train_dic[image_id] = dict()
        train_dic[image_id]["image_info"] = image_info

In [36]:
def add_anno_info(anno_info):
    global train_dic
    
    image_id = anno_info['image_id']
    if image_id not in train_dic.keys():
        print("loss image id! Image id is " + str(image_id))
    else:
        category_id = anno_info['category_id']

        if ("anno" not in train_dic[image_id].keys()):
            train_dic[image_id]["anno"] = []
        train_dic[image_id]["anno"].append(anno_info)       

In [37]:
for image_info in image_infos:
    add_image_info(image_info)
for anno_info in anno_infos:
    add_anno_info(anno_info)

In [38]:
train_dic

{20485447352320001: {'image_info': {'license': 1,
   'file_name': '031_4875.png',
   'width': 1280,
   'id': 20485447352320001,
   'height': 720},
  'anno': [{'area': 360,
    'category_id': 12,
    'bbox': [283, 311, 30, 12],
    'iscrowd': 0,
    'segmentation': [283, 311, 283, 323, 313, 311, 313, 323],
    'id': 20486024996061191,
    'image_id': 20485447352320001},
   {'area': 725,
    'category_id': 33,
    'bbox': [1110, 167, 25, 29],
    'iscrowd': 0,
    'segmentation': [1110, 167, 1110, 196, 1135, 167, 1135, 196],
    'id': 20486024996061192,
    'image_id': 20485447352320001},
   {'area': 192,
    'category_id': 9,
    'bbox': [495, 262, 6, 32],
    'iscrowd': 0,
    'segmentation': [495, 262, 495, 294, 501, 262, 501, 294],
    'id': 20486024996061193,
    'image_id': 20485447352320001},
   {'area': 2964,
    'category_id': 1,
    'bbox': [1145, 237, 52, 57],
    'iscrowd': 0,
    'segmentation': [1145, 237, 1145, 294, 1197, 237, 1197, 294],
    'id': 20486024996061194,
    '

#### 计算每一张图各类别数量

In [44]:
cat_dic = dict()

for keyId in train_dic.keys():
    
    cats_num = np.zeros(74)
    
    item = train_dic[keyId]
    annos = item["anno"]
    for anno in annos:
        cat_id = anno['category_id']
        cats_num[cat_id-1] += 1
        
    cat_dic[keyId] = dict()
    cat_dic[keyId]["cats_num"] = cats_num
    cat_dic[keyId]["total_num"] = np.sum(cats_num)
    cat_dic[keyId]["rare_num"] = np.sum(cats_num[12:])
    cat_dic[keyId]["rare_part"] = cat_dic[keyId]["rare_num"]/cat_dic[keyId]["total_num"]

In [45]:
cat_dic

{20485447352320001: {'cats_num': array([3., 1., 0., 0., 0., 0., 0., 0., 2., 0., 0., 4., 0., 0., 0., 0., 0.,
         0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 2., 0.,
         0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0., 0., 0., 0., 0.]),
  'total_num': 12.0,
  'rare_num': 2.0,
  'rare_part': 0.16666666666666666},
 20485448891629574: {'cats_num': array([2., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0., 0., 0., 0., 0.]),
  'total_num': 2.0,
  'rare_num': 0.0,
  'rare_part': 0.0},
 20485450363830280: {'cats_num': array([0., 0., 0., 0., 3., 0., 0., 0., 2., 0., 0., 0., 0., 0., 0., 0., 0.,
       

In [47]:
updata_label_number = label_number

In [48]:
updata_label_number

array([ 8832,  2464,   452,   314,  1282,   738,   652,   534,  3226,
        1304,   322, 10886,   582,    30,   456,   110,     0,   138,
         100,     6,   222,   130,     0,     0,     0,     0,    24,
         408,    44,    34,   308,     0,   350,     8,    24,    58,
          72,    70,    42,    78,    44,    24,    86,   204,     0,
           4,    76,    20,    40,   160,    52,    30,     0,     0,
           0,   136,   154,    46,     0,     0,     0,     0,     0,
           0,     6,     0,     8,    22,     0,     2,    84,     0,
          26,     0])